## 실거래가 전처리
1. 주요 전처리 항목
- 내부 테스트, 검수용 등 내부테스트용 쿠폰이 들어간 경우는 전부 데이터에서 지웠습니다.
    - 단, 내부 복지용으로 제공된 것들은 어떻게 해야될 지 잘 모르겠습니다.
- 실거래가 음수인 항목 전부 뺐습니다.


In [9]:
# library import
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
import plotly.express as px

# 한글 깨짐 방지
import matplotlib as mpl
mpl.rcParams['font.family'] = 'AppleGothic'
mpl.rcParams['axes.unicode_minus'] = False #제발 #그만좀 #깨져라


df = pd.read_csv('./eda-proj-fc-purchase.csv') ## 데이터파일 경로를 넣어주세요
print(df.shape)
def replace_dash_with_value(df, columns):
    for col in columns:
        df[col] = df.apply(lambda row: '0' if isinstance(row[col], str) and row[col] == '-' else row[col], axis=1)
        df[col] = df[col].astype(int)
    return df
columns = ['판매가격', '환불금액', '실거래금액', '거래금액', '쿠폰할인액']
df = replace_dash_with_value(df, columns)


# 데이터타입 int로 변경 - by 혜영님
df[["판매가격", "실거래금액", "거래금액", "환불금액", "쿠폰할인액"]] = df[["판매가격", "실거래금액", "거래금액", "환불금액", "쿠폰할인액"]].replace("-", 0, regex=True).astype(int)

# 시간 데이터타입 변경 - by 도성님
df['date'] = df['거래일자'].str[:-11]

df['date'] = df['date'].str.replace('.','-')

df['date'] = df['date'].str.replace(' ','')

df['date'] = df['date'].str[:-1]
# 날짜데이터 정리.
df['date']
df['time'] = df['거래일자'].str[12:]

df['time'] = df['time'].str.replace('.','')
df['time'] = df['time'].str.replace('오전','AM')
df['time'] = df['time'].str.replace('오후','PM')
df['time'] = df['time'].str.lstrip()

df['time'].values
from datetime import datetime, timedelta

def convert_time_to_24h(time_str):
    # Parse the time string into a datetime object
    time_obj = datetime.strptime(time_str, '%p %I:%M:%S')

    # If the time is in the afternoon, add 12 hours to it
    if 'pm' in time_str.lower():
        time_obj += timedelta(hours=12)

    # Format the datetime object back into a string in the desired format
    return time_obj.strftime('%H:%M:%S')

# Apply the function to the 'time' column in the DataFrame
df['time'] = df['time'].apply(convert_time_to_24h)

df['time']
df['date_time'] = df['date'] + ' ' + df['time']
df['date_time']
df['date_time'] = pd.to_datetime(df['date_time'], format='%Y-%m-%d %H:%M:%S')
df['date_time']

(159328, 16)


0        2022-12-31 10:12:33
1        2022-12-30 06:12:57
2        2022-12-31 11:12:15
3        2022-12-31 11:12:03
4        2022-12-31 11:12:10
                 ...        
159323   2022-01-01 00:01:08
159324   2022-01-01 00:01:12
159325   2022-01-01 00:01:21
159326   2022-01-02 11:01:24
159327   2022-01-24 04:01:00
Name: date_time, Length: 159328, dtype: datetime64[ns]

In [10]:
lt = df[df['실거래금액'] >= 0].sort_values(by='실거래금액', ascending=False)
# 0과 양수를 데이터로 가지고, 음수 데이터(환불)을 제외한 실거래금액.
# 0 또는 양수인 실거래금액에서 환불이 아닌 것 확인 완료.

# m_lt = df[df['실거래금액'] < 0] # 음수 데이터프레임. 참고용.
# 실거래가 음수인 값에서는 PAYMENT 에 해당하는 값 없음 확인 완료.


expromo = lt[~(lt['결제수단'].str.contains('PROMO')) & ~(lt['코스(상품) 이름'].str.contains('test_qa'))]
# 실거래금액이 0 이상인 데이터에서, PROMOTION 을 제외한 결제수단들. 추가로, 코스이름중 test_qa 도 제외함. 132963 행

# 프로모션으로 판매된 데이터는 실거래금액이 없으므로 제외하는 게 맞을 것 같습니다.
# 내부용으로 제공된 쿠폰 등에 대해서는 다른 팀원분들과의 의견 공유가 필요합니다.
# 검수용, 검토용, test용 등 내부점검용으로 사용된 쿠폰, 강사님 쿠폰도 프로모션으로 적용됩니다.
## 우선 내부점검용으로 사용된 쿠폰, 강사님에게 제공된 쿠폰은 포함하고 나머지는 날리겠습니다.

mask1 = ~(df['코스(상품) 이름'].str.contains('test')) & (df['결제수단'].str.contains('PROMO')) & ~(df['쿠폰이름'].str.contains('TEST|test|검토|검수|점검')) & ~(df['쿠폰이름'].str.contains('(test|검수|검토|(?<!코딩)테스트)'))
# expromo 와 다르게 전체 데이터에서 뽑아낸 이유: 프로모션 쿠폰이 제공된 경우는 실거래금액이 모두 0입니다.
# 전체 데이터프레임에서, '결제수단' 이 프로모션 and 쿠폰이름에 test, 검토, 검수, 점검 단어가 들어간 경우 제외했습니다.
# 쿠폰이름에 '코딩테스트' 가 있는 경우는 포함했고, 원래 데이터에서 지워도 상관없는 것 확인했습니다.

fff = df[mask1] # 위의 조건을 건 새로운 데이터프레임


filtered_df = pd.concat([expromo, fff]).sort_values('거래id') # 두 데이터프레임 합치기

/var/folders/21/l0xnhml970ng2wb3f9rky3fh0000gn/T/ipykernel_20611/2825105908.py:17: UserWarning:

This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.



In [11]:
final_df = filtered_df[filtered_df['실거래금액'] <= filtered_df['판매가격']]
# 개인 사용자의 구매만 필요하고, b2b 거래를 제외하려면(용담임쌤피셜) 이렇게 하면 될 것 같음.

final_df

거래id       유형   고객id    코스ID         사이트   포맷      카테고리   
159326  1545070  PAYMENT  19606  208104  FASTCAMPUS  올인원    업무 생산성  \
159325  1551361  PAYMENT  12764  202927  FASTCAMPUS  올인원  데이터 사이언스   
159324  1551410  PAYMENT  95136  206811  FASTCAMPUS  올인원     영상/3D   
159323  1551424  PAYMENT  39658  204491  FASTCAMPUS  올인원     부업/창업   
159322  1551425  PAYMENT  20990  204366  FASTCAMPUS  올인원       마케팅   
...         ...      ...    ...     ...         ...  ...       ...   
4       2413887  PAYMENT  94328  210773  FASTCAMPUS  올인원     프로그래밍   
3       2413891  PAYMENT  41898  213450  FASTCAMPUS  올인원     프로그래밍   
2       2413897  PAYMENT  18075  211782  FASTCAMPUS  올인원     영상/3D   
1       2415408  PAYMENT  58309  210664  FASTCAMPUS  올인원    부동산/금융   
0       2417084  PAYMENT  20053  209016  FASTCAMPUS  올인원    업무 생산성   

                                                코스(상품) 이름   
159326               올인원 패키지 : 100억을 움직이는 50가지 PPT 디자인 원칙  \
159325                올인원 패키지 : 파이썬을 활용한 데이터 전처리 Level UP   
159324  [Kit] 닷밀의 미디어아트 그래픽 클래스 : 모션그래픽 뉴패러다임 Creative...   
159323            올인원 패키지 : 제 2의 월급을 만들어주는 직장인 스몰비즈니스 가이드   
159322                 올인원 패키지 : 30개 글감으로 에세이 작가되기 BY.정영욱   
...                                                   ...   
4                 초격차 패키지 : 개발자 취업 합격 패스 With 코딩테스트, 기술면접   
3       초격차 패키지 : 35개 프로젝트로 배우는 Android 앱 개발 feat. Jet...   
2       편집하는여자의 영상편집 마스터클래스 - 제 6강 다양한 효과를 응용하여 애프터이펙트...   
1                        초격차 패키지 : 한 번에 끝내는 부동산 금융(PF) 실무   
0                            올인원 패키지 : 김왼손의 파이썬 업무자동화 유치원   

                             거래일자                            쿠폰이름    판매가격   
159326    2022. 1. 2. 오전 11:01:24                               -  289000  \
159325    2022. 1. 1. 오전 12:01:21    [WELCOME] 패캠은 처음이지? 3만원 할인쿠폰  166000   
159324    2022. 1. 1. 오전 12:01:12                               -  385000   
159323    2022. 1. 1. 오전 12:01:08  [NEW22] 온라인 강의 1만원 즉시 추가 할인 쿠폰  217000   
159322    2022. 1. 1. 오전 12:01:34                               -  137000   
...                           ...                             ...     ...   
4       2022. 12. 31. 오후 11:12:10                               -  239000   
3       2022. 12. 31. 오후 11:12:03           [WELCOME] 프로그래밍 3만원할인  165000   
2       2022. 12. 31. 오후 11:12:15                               -  549000   
1        2022. 12. 30. 오후 6:12:57                               -  501000   
0       2022. 12. 31. 오후 10:12:33                               -  189000   

            결제수단   실거래금액  쿠폰할인액    거래금액  환불금액        date      time   
159326     VBANK  289000      0  289000     0    2022-1-2  11:01:24  \
159325      CARD  136000  30000  136000     0    2022-1-1  00:01:21   
159324      CARD  385000      0  385000     0    2022-1-1  00:01:12   
159323      CARD  207000  10000  207000     0    2022-1-1  00:01:08   
159322      CARD  137000      0  137000     0    2022-1-1  00:01:34   
...          ...     ...    ...     ...   ...         ...       ...   
4           CARD  239000      0  239000     0  2022-12-31  11:12:10   
3           CARD  135000  30000  135000     0  2022-12-31  11:12:03   
2           CARD  549000      0  549000     0  2022-12-31  11:12:15   
1       TRANSFER  501000      0  501000     0  2022-12-30  06:12:57   
0       TRANSFER  159000      0  159000     0  2022-12-31  10:12:33   

                 date_time  
159326 2022-01-02 11:01:24  
159325 2022-01-01 00:01:21  
159324 2022-01-01 00:01:12  
159323 2022-01-01 00:01:08  
159322 2022-01-01 00:01:34  
...                    ...  
4      2022-12-31 11:12:10  
3      2022-12-31 11:12:03  
2      2022-12-31 11:12:15  
1      2022-12-30 06:12:57  
0      2022-12-31 10:12:33  

[147414 rows x 19 columns]

In [12]:
# 대강 그려보자.
x1 = final_df['카테고리']
y1 = final_df['실거래금액']

fig = px.box(df, x=x1, y=y1, title='카테고리별 실거래금액',labels={'x':'카테고리', 'y':'실거래금액'})

display(final_df, fig.show())
# 이상치들이 꽤 남아있는 것 같다..조금 더 정제가 필요한 것 같기도?

거래id       유형   고객id    코스ID         사이트   포맷      카테고리   
159326  1545070  PAYMENT  19606  208104  FASTCAMPUS  올인원    업무 생산성  \
159325  1551361  PAYMENT  12764  202927  FASTCAMPUS  올인원  데이터 사이언스   
159324  1551410  PAYMENT  95136  206811  FASTCAMPUS  올인원     영상/3D   
159323  1551424  PAYMENT  39658  204491  FASTCAMPUS  올인원     부업/창업   
159322  1551425  PAYMENT  20990  204366  FASTCAMPUS  올인원       마케팅   
...         ...      ...    ...     ...         ...  ...       ...   
4       2413887  PAYMENT  94328  210773  FASTCAMPUS  올인원     프로그래밍   
3       2413891  PAYMENT  41898  213450  FASTCAMPUS  올인원     프로그래밍   
2       2413897  PAYMENT  18075  211782  FASTCAMPUS  올인원     영상/3D   
1       2415408  PAYMENT  58309  210664  FASTCAMPUS  올인원    부동산/금융   
0       2417084  PAYMENT  20053  209016  FASTCAMPUS  올인원    업무 생산성   

                                                코스(상품) 이름   
159326               올인원 패키지 : 100억을 움직이는 50가지 PPT 디자인 원칙  \
159325                올인원 패키지 : 파이썬을 활용한 데이터 전처리 Level UP   
159324  [Kit] 닷밀의 미디어아트 그래픽 클래스 : 모션그래픽 뉴패러다임 Creative...   
159323            올인원 패키지 : 제 2의 월급을 만들어주는 직장인 스몰비즈니스 가이드   
159322                 올인원 패키지 : 30개 글감으로 에세이 작가되기 BY.정영욱   
...                                                   ...   
4                 초격차 패키지 : 개발자 취업 합격 패스 With 코딩테스트, 기술면접   
3       초격차 패키지 : 35개 프로젝트로 배우는 Android 앱 개발 feat. Jet...   
2       편집하는여자의 영상편집 마스터클래스 - 제 6강 다양한 효과를 응용하여 애프터이펙트...   
1                        초격차 패키지 : 한 번에 끝내는 부동산 금융(PF) 실무   
0                            올인원 패키지 : 김왼손의 파이썬 업무자동화 유치원   

                             거래일자                            쿠폰이름    판매가격   
159326    2022. 1. 2. 오전 11:01:24                               -  289000  \
159325    2022. 1. 1. 오전 12:01:21    [WELCOME] 패캠은 처음이지? 3만원 할인쿠폰  166000   
159324    2022. 1. 1. 오전 12:01:12                               -  385000   
159323    2022. 1. 1. 오전 12:01:08  [NEW22] 온라인 강의 1만원 즉시 추가 할인 쿠폰  217000   
159322    2022. 1. 1. 오전 12:01:34                               -  137000   
...                           ...                             ...     ...   
4       2022. 12. 31. 오후 11:12:10                               -  239000   
3       2022. 12. 31. 오후 11:12:03           [WELCOME] 프로그래밍 3만원할인  165000   
2       2022. 12. 31. 오후 11:12:15                               -  549000   
1        2022. 12. 30. 오후 6:12:57                               -  501000   
0       2022. 12. 31. 오후 10:12:33                               -  189000   

            결제수단   실거래금액  쿠폰할인액    거래금액  환불금액        date      time   
159326     VBANK  289000      0  289000     0    2022-1-2  11:01:24  \
159325      CARD  136000  30000  136000     0    2022-1-1  00:01:21   
159324      CARD  385000      0  385000     0    2022-1-1  00:01:12   
159323      CARD  207000  10000  207000     0    2022-1-1  00:01:08   
159322      CARD  137000      0  137000     0    2022-1-1  00:01:34   
...          ...     ...    ...     ...   ...         ...       ...   
4           CARD  239000      0  239000     0  2022-12-31  11:12:10   
3           CARD  135000  30000  135000     0  2022-12-31  11:12:03   
2           CARD  549000      0  549000     0  2022-12-31  11:12:15   
1       TRANSFER  501000      0  501000     0  2022-12-30  06:12:57   
0       TRANSFER  159000      0  159000     0  2022-12-31  10:12:33   

                 date_time  
159326 2022-01-02 11:01:24  
159325 2022-01-01 00:01:21  
159324 2022-01-01 00:01:12  
159323 2022-01-01 00:01:08  
159322 2022-01-01 00:01:34  
...                    ...  
4      2022-12-31 11:12:10  
3      2022-12-31 11:12:03  
2      2022-12-31 11:12:15  
1      2022-12-30 06:12:57  
0      2022-12-31 10:12:33  

[147414 rows x 19 columns]

None